# Extend the SVM Prediction model to other datasets

In [1]:
%%javascript
function getQueryStringValue (key)
{  
    return unescape(window.location.search.replace(new RegExp("^(?:.*[&\\?]" + escape(key).replace(/[\.\+\*]/g, "\\$&") + "(?:\\=([^&]*))?)?.*$", "i"), "$1"));
}
IPython.notebook.kernel.execute("survey_url='".concat(getQueryStringValue("surveyurl")).concat("'"));
IPython.notebook.kernel.execute("views='".concat(getQueryStringValue("views")).concat("'"));
IPython.notebook.kernel.execute("view='".concat(getQueryStringValue("view")).concat("'"));
IPython.notebook.kernel.execute("user='".concat(getQueryStringValue("user")).concat("'"));
IPython.notebook.kernel.execute("csv_file='".concat(getQueryStringValue("csv")).concat("'")); 
IPython.notebook.kernel.execute("dzc_file='".concat(getQueryStringValue("dzc")).concat("'")); 
IPython.notebook.kernel.execute("params='".concat(getQueryStringValue("params")).concat("'")); 
IPython.notebook.kernel.execute("active_object='".concat(getQueryStringValue("activeobject")).concat("'")); 
IPython.notebook.kernel.execute("full_notebook_url='" + window.location + "'"); 

<IPython.core.display.Javascript object>

In [2]:
import warnings
warnings.filterwarnings('ignore')  # "error", "ignore", "always", "default", "module" or "once"

# More imports
import matplotlib.pyplot as plt
import numpy as np
import argparse
import random
import csv
import pandas as pd
import re
import cv2
import os

# import the necessary packages for SVM predictor
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import LinearSVC
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
import imutils
import joblib

# import histogram func
from histogram import Histograms

# Import widget functionality
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets


import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin

In [3]:
# init the image suffix, yset, and image list
suffix = '.jpg'
img_list = []
yset = []
# create labels list and 2 dicts for 2 way mapping
labels = []

In [4]:
# use csv file to grab images/labels
csv_path = "/home/jovyan/temp_csvs/" + csv_file
df = pd.read_csv(csv_path)

#generate image path
#lower_case_csv = csv_file.lower()
#img_path = "../../images/" + lower_case_csv.split(".")[0]

localdzc = dzc_file.replace("https://maxim.ucsd.edu/dzgen/lib-staging-uploads","/lib-nfs/dzgen")
full_images_location = localdzc.replace("/content.dzc","/full_images/")

from bs4 import BeautifulSoup
from urllib.parse import urljoin

response = requests.get(full_images_location)
soup = BeautifulSoup(response.text, 'html.parser')

image_links = soup.find_all('a', href=True)

image_urls = []

def get_string_before_last_period(input_string):
    parts = input_string.rsplit('.', 1)
    if len(parts) > 1:
        return parts[0]
    else:
        return input_string

images_in_df = list(df["#img"].unique())

for link in image_links:
    image_url = link['href']
    if get_string_before_last_period(image_url) in images_in_df:
    
        if not image_url.startswith(('http:', 'https:')):
            full_image_url = urljoin(full_images_location, image_url)
        else:
            full_image_url = image_url

        image_urls.append(full_image_url)
model2 = joblib.load('/home/jovyan/myclone/operations/svm/svmModel.pkl') 

ModuleNotFoundError: No module named 'sklearn.svm.classes'

In [5]:
# Choose model for prediction
models = os.listdir("./models/")

mod_menu = {}
for i in range(0, len(models)):
    mod_menu[models[i]] = models[i]

def f(Models):
    return Models

out2 = interact(f, Models=mod_menu)

interactive(children=(Dropdown(description='Models', options={'zaslavsk_svm_Petrographic Fabric_1.pkl': 'zasla…

In [8]:
#select model
modelName = out2.widget.result
model2 = joblib.load(os.path.join('models/', modelName))

#get label and typeH
def getParams(model):
    label_array1 = model.split("svm_")
    label_array2 = label_array1[1].split("_")
    label = label_array2[0] 
    typeH = label_array2[1].split(".")[0]
    return [label, typeH]

modelParams = getParams(modelName)  

In [9]:
# grab chosen column names
nameCol = df['#img']
predCol = df[modelParams[0]]
typeH = int(modelParams[1])

# add all fabric columns to the y set
for i in range (0,len(predCol)):
    np.append(labels,predCol[i])
# create new hist_list
hist_list = []
# gather images from path created from file names in csv file

for i in range (0,len(nameCol)):
    image_name = nameCol[i]
    url = full_images_location + image_name + ".png"
    response = requests.get(url)

    image_bytes = np.frombuffer(response.content, np.uint8)
    im = cv2.imdecode(image_bytes, cv2.IMREAD_COLOR)
    labels.append(predCol[i])
    hist_list.append(im)
    
    if typeH == 0:
        hist = Histograms.extract_color_histogram(im)
    elif typeH == 1: 
        hist = Histograms.extract_blue_histogram(im)
    elif typeH == 2: 
        hist = Histograms.extract_red_histogram(im)
    elif typeH == 3: 
        hist = Histograms.extract_green_histogram(im)
    hist_list.append(hist)
    
# transform labels into numerical system
le = LabelEncoder()
labels = le.fit_transform(predCol)
 

# Calculate predictions on the data set
predictions = model2.predict(np.array(hist_list))
print(classification_report(labels, predictions, target_names = le.classes_))

ValueError: setting an array element with a sequence.

In [12]:
import requests
import cv2
import numpy as np
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report
from sklearn.svm import SVC

# Load your CSV data into a DataFrame (assuming you've already done this)
# Example: df = pd.read_csv('your_data.csv')

# Assuming you have a DataFrame 'df' with columns '#img', 'modelParams[0]', and 'modelParams[1]'
nameCol = df['#img']
predCol = df[modelParams[0]]
typeH = int(modelParams[1])

# Initialize lists for labels, images, and histograms
labels = []
image_list = []
histogram_list = []


# Loop through the DataFrame rows
for i in range(len(nameCol)):
    image_name = nameCol[i]
    url = full_images_location + image_name + ".png"

    response = requests.get(url)

    if response.status_code == 200:
        # Read the image from the response content
        image_bytes = np.frombuffer(response.content, np.uint8)
        im = cv2.imdecode(image_bytes, cv2.IMREAD_COLOR)

        if im is not None:
            labels.append(predCol[i])
            image_list.append(im)

            # Extract histograms based on 'typeH'
            if typeH == 0:
                hist = Histograms.extract_color_histogram(im)
            elif typeH == 1:
                hist = Histograms.extract_blue_histogram(im)
            elif typeH == 2:
                hist = Histograms.extract_red_histogram(im)
            elif typeH == 3:
                hist = Histograms.extract_green_histogram(im)

            histogram_list.append(hist)
        else:
            print(f"Error reading image from URL: {url}")
    else:
        print(f"Failed to fetch image from URL: {url}")

# Convert labels to numerical values
le = LabelEncoder()
labels = le.fit_transform(labels)

# Convert lists to NumPy arrays
image_array = np.array(image_list)
histogram_array = np.array(histogram_list)

# Concatenate image and histogram arrays if needed (e.g., horizontally)
combined_array = np.hstack((image_array, histogram_array))

# Load your SVM model (replace 'YourSVMModel.pkl' with your model filename)
model2 = joblib.load('YourSVMModel.pkl')

# Make predictions
predictions = model2.predict(combined_array)
print(classification_report(labels, predictions, target_names=le.classes_))


ValueError: all the input arrays must have same number of dimensions, but the array at index 0 has 4 dimension(s) and the array at index 1 has 2 dimension(s)

In [14]:
histogram_list

[array([1.60557788e-03, 2.59725843e-04, 5.66674513e-04, 8.02788942e-04,
        7.55566056e-04, 6.37508871e-04, 8.97234713e-04, 1.39307487e-03,
        1.72363501e-03, 2.62086978e-03, 2.24308670e-03, 2.88059562e-03,
        2.80976132e-03, 4.48617339e-03, 4.86395648e-03, 5.64313401e-03,
        7.34315766e-03, 8.80706683e-03, 9.37374122e-03, 9.65707842e-03,
        1.06959818e-02, 1.04362564e-02, 1.14043253e-02, 1.30807376e-02,
        1.40960291e-02, 1.40251946e-02, 1.37418574e-02, 1.40960291e-02,
        1.40251946e-02, 0.00000000e+00, 1.30099030e-02, 1.22307260e-02,
        1.19709997e-02, 9.63346753e-03, 9.44457576e-03, 8.02788977e-03,
        6.96537457e-03, 7.50843761e-03, 5.83202532e-03, 5.97369391e-03,
        5.73757989e-03, 5.50146541e-03, 5.17090503e-03, 4.46256204e-03,
        5.07645961e-03, 4.43895068e-03, 4.36811615e-03, 4.91117919e-03,
        4.41533932e-03, 4.48617339e-03, 4.10839031e-03, 4.34450479e-03,
        4.29728208e-03, 4.20283619e-03, 4.22644755e-03, 3.588938

In [21]:
import requests
import cv2
import numpy as np
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVC
from sklearn.metrics import classification_report

# grab chosen column names
nameCol = df['#img']
predCol = df[modelParams[0]]
typeH = int(modelParams[1])

# add all fabric columns to the y set
for i in range (0,len(predCol)):
    np.append(labels,predCol[i])
# create new hist_list
hist_list = []
# gather images from path created from file names in csv file

for i in range(0, len(nameCol)):
    image_name = nameCol[i]
    url = full_images_location + image_name + ".png"
    response = requests.get(url)

    image_bytes = np.frombuffer(response.content, np.uint8)
    im = cv2.imdecode(image_bytes, cv2.IMREAD_COLOR)
    
    if im is not None:
        labels.append(predCol[i])
        image_list.append(im)

        if typeH == 0:
            hist = Histograms.extract_color_histogram(im)
        elif typeH == 1:
            hist = Histograms.extract_blue_histogram(im)
        elif typeH == 2:
            hist = Histograms.extract_red_histogram(im)
        elif typeH == 3:
            hist = Histograms.extract_green_histogram(im)
        histogram_list.append(hist)
    else:
        print(f"Error reading image from URL: {url}")

# Convert labels to numerical values
le = LabelEncoder()
labels = le.fit_transform(labels)

# Convert lists to NumPy arrays
image_array = np.array(image_list)
histogram_array = np.array(histogram_list)

# Combine the image array and histogram array if needed
# hist_list = np.hstack((image_array, histogram_array))

# Load your SVM model (model2) here

# Make predictions
# predictions = model2.predict(hist_list)
# print(classification_report(labels, predictions, target_names=le.classes_))


AttributeError: 'numpy.ndarray' object has no attribute 'append'

In [ ]:
# Translate back to original csv label names
predictionsMade = list(le.inverse_transform(predictions))
finalPred = []
for i in range (0,len(predictionsMade)):
    finalPred.append(predictionsMade[i])

from IPython.display import display
input_text = widgets.Text(
    value=None,
    placeholder='Type label here',
    disabled=False
)
output_text = widgets.Text(
    value=None,
    placeholder='New Header will be displayed here',
    disabled=False
)

def bind_input_to_output(sender):
    output_text.value = input_text.value

input_text.observe(bind_input_to_output)

print("Input new column Header Label: ")

display(input_text)
display(output_text)

In [14]:
# Append the new column w/ it's new column name
df[input_text.value] = finalPred

# new file name
new_file =  csv_file[:-4]+'_v1.csv'
df.to_csv(new_file, index=None)

In [19]:
#Input survey name

from IPython.display import display
input_text = widgets.Text()
output_text = widgets.Text()

def bind_input_to_output(sender):
    output_text.value = input_text.value

# Tell the text input widget to call bind_input_to_output() on submit
input_text.observe(bind_input_to_output)

print("Input survey name here:")
# Display input text box widget for input
display(input_text)

display(output_text)

Input survey name here:


Text(value='')

Text(value='')

In [75]:
#Print survey name
survey_name = output_text.value
print("Survey name is:", survey_name)

Survey name is: komm_2


In [88]:
#Parse url
upload_url = survey_url.split("/main")

new_survey_url = survey_url.split(user)

new_survey_views = survey_url.split(".csv")

https://suave-dev.sdsc.edu
https://suave-dev.sdsc.edu/main/file=



In [21]:
import requests
upload_url = upload_url[0] + ":3001/uploadCSV"
upload_data = {'name': input_text.value, 'dzc': dzc_file, 'user':user}
files = {"file": open(new_file, "rb")}
r = requests.post(upload_url, files=files, data=upload_data)
print(r.status_code, r.reason)

regex = re.compile('[^0-9a-zA-Z_]')
survey_url = survey_name
survey_url =  regex.sub('_', survey_url)

url = new_survey_url[0] + user + "_" + input_text.value + ".csv" + "&views=" + views + "&view=" + view
print(url)

ConnectionError: HTTPConnectionPool(host='localhost', port=3001): Max retries exceeded with url: /uploadCSV (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7f751eb34828>: Failed to establish a new connection: [Errno 111] Connection refused',))